In [159]:
import pandas as pd
import numpy as np

import plotly.graph_objects as go
from plotly.subplots import make_subplots
from pathlib import Path

from predict_energy_behavior.models.joined_model import JoinedModel

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [160]:
df = pd.read_parquet(
    "/beegfs/ws/0/s4610340-energy_behavior/yahor/kaggle-predict_energy_behavior_of_prosumers/data/processed/train/make_features/df_features.parquet",
    engine="fastparquet"
).dropna()
df = df.loc[df["is_consumption"]==0] # select production
df

county is_business product_type is_consumption            datetime  \
row_id                                                                       
412848       0           0            1              0 2022-01-16 00:00:00   
412978       0           0            1              0 2022-01-16 01:00:00   
413108       0           0            1              0 2022-01-16 02:00:00   
413238       0           0            1              0 2022-01-16 03:00:00   
413368       0           0            1              0 2022-01-16 04:00:00   
...        ...         ...          ...            ...                 ...   
2017818     14           1            2              0 2023-05-31 19:00:00   
2017948     14           1            2              0 2023-05-31 20:00:00   
2018078     14           1            2              0 2023-05-31 21:00:00   
2018208     14           1            2              0 2023-05-31 22:00:00   
2018338     14           1            2              0 2023-05-31 23:00:00   

              date  dayofyear  hour  day  weekday  ...  \
row_id                                             ...   
412848  2022-01-16         16     0   16        7  ...   
412978  2022-01-16         16     1   16        7  ...   
413108  2022-01-16         16     2   16        7  ...   
413238  2022-01-16         16     3   16        7  ...   
413368  2022-01-16         16     4   16        7  ...   
...            ...        ...   ...  ...      ...  ...   
2017818 2023-05-31        151    19   31        3  ...   
2017948 2023-05-31        151    20   31        3  ...   
2018078 2023-05-31        151    21   31        3  ...   
2018208 2023-05-31        151    22   31        3  ...   
2018338 2023-05-31        151    23   31        3  ...   

         diff_168h_10_metre_u_wind_component_historical  \
row_id                                                    
412848                                        -0.409545   
412978                                         0.643126   
413108                                        -0.566723   
413238                                        -2.125504   
413368                                        -0.549850   
...                                                 ...   
2017818                                       -0.298044   
2017948                                       -0.665162   
2018078                                        0.315522   
2018208                                        0.510262   
2018338                                       -0.329075   

         diff_168h_10_metre_u_wind_component_forecast  \
row_id                                                  
412848                                       6.771800   
412978                                       6.784103   
413108                                       3.771397   
413238                                       2.513531   
413368                                       1.969852   
...                                               ...   
2017818                                      4.869689   
2017948                                      4.048730   
2018078                                      3.727382   
2018208                                      3.873753   
2018338                                      3.483533   

        diff_168h_10_metre_v_wind_component_historical  \
row_id                                                   
412848                                       -0.595874   
412978                                        0.787342   
413108                                       -1.037029   
413238                                       -0.375098   
413368                                        1.754773   
...                                                ...   
2017818                                       0.113850   
2017948                                       0.498659   
2018078                                       0.606830   
2018208                                      -0.467229   
2018338                         

In [161]:
df["target_per_capacity"] = df["target"] / df["installed_capacity"]

In [162]:
df["snowfall_integrated_24h_historical"].describe()

count    8.027520e+05
mean     4.040130e-01
std      5.826018e-01
min     -5.107026e-15
25%     -3.608225e-16
50%      6.689094e-15
75%      7.000000e-01
max      4.500000e+00
Name: snowfall_integrated_24h_historical, dtype: float64

In [163]:
def viz_weather_and_predictions_for_month(df, year: int, month: int):
    t_start = pd.Timestamp(year=year, month=month, day=1)
    t_end = t_start + pd.DateOffset(months=1)
    df_this_year = df.loc[
        (df["datetime"] > t_start) &
        (df["datetime"] < t_end)
    ]
    df_last_year = df.loc[
        (df["datetime"] > (t_start - pd.DateOffset(years=1))) &
        (df["datetime"] < (t_end - pd.DateOffset(years=1)))
    ]
    df_last_year = df_last_year.assign(**{"datetime": df_last_year["datetime"] + pd.DateOffset(years=1)})
    
    fig = make_subplots(cols=1, rows=7, subplot_titles=["Temperature", "Rain", "Snowfall", "I", "target", "snowfall int 48h", "rain int 48h"], shared_xaxes=True)
    
    for df, opacity in zip([df_this_year, df_last_year], [1, 0.5]):
        # Temperature
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["temperature_forecast"], marker_color="blue", name="forecast", legendgroup=1, opacity=opacity),
            row=1, col=1
        )
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["temperature_historical"], marker_color="red", name="historical", legendgroup=2, opacity=opacity),
            row=1, col=1
        )

        # Rain
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["rain_forecast"], marker_color="blue", name="forecast", legendgroup=1, showlegend=False, opacity=opacity),
            row=2, col=1
        )
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["rain_historical"], marker_color="red", name="historical", legendgroup=2, showlegend=False, opacity=opacity),
            row=2, col=1
        )

        # Snow
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["snowfall_forecast"], marker_color="blue", name="forecast", legendgroup=1, showlegend=False, opacity=opacity),
            row=3, col=1
        )
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["snowfall_historical"], marker_color="red", name="historical", legendgroup=2, showlegend=False, opacity=opacity),
            row=3, col=1
        )

        # I
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["surface_solar_radiation_downwards_forecast"], marker_color="blue", name="forecast", legendgroup=1, showlegend=False, opacity=opacity),
            row=4, col=1
        )


        # target
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["target"] / df["installed_capacity"], marker_color="green", name="target", showlegend=True, opacity=opacity),
            row=5, col=1
        )
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["predictions"] / df["installed_capacity"], marker_color="orange", name="predictions", showlegend=True, opacity=opacity),
            row=5, col=1
        )

        # Snowfall integrated
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["snowfall_integrated_24h_forecast"], marker_color="blue", name="forecast", legendgroup=1, showlegend=False, opacity=opacity),
            row=6, col=1
        )
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["snowfall_integrated_24h_historical"], marker_color="red", name="historical", legendgroup=2, showlegend=False, opacity=opacity),
            row=6, col=1
        )

         # Rain integrated
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["rain_integrated_24h_forecast"], marker_color="blue", name="forecast", legendgroup=1, showlegend=False, opacity=opacity),
            row=7, col=1
        )
        fig.add_trace(
            go.Scatter(x=df["datetime"], y=df["rain_integrated_24h_historical"], marker_color="red", name="historical", legendgroup=2, showlegend=False, opacity=opacity),
            row=7, col=1
        )

    fig.update_layout(height=800)

    return fig

In [164]:
model = JoinedModel.load(Path("/beegfs/ws/0/s4610340-energy_behavior/yahor/kaggle-predict_energy_behavior_of_prosumers/outputs/train/lgbm-wlf+diff-lgbms-submit/model_joined-f-2022-12"))
model

In [165]:
model._model_p, model._model_c

(<predict_energy_behavior.models.production.two_orders_regression.AvgTwoOrdersRegression at 0x7f0eebc25db0>,
 <predict_energy_behavior.models.consumption.lgbm_regression.LGBMOnMultiDiff at 0x7f0eebc33850>)

In [166]:
df["predictions"] = model.predict(df)

In [167]:
df["predictions_per_capacity"] = df["predictions"] / df["installed_capacity"]

In [168]:
def calculate_dep(df, x: str, y: str, win, step, val_thr):
    series = df.set_index(df[x] / df[x].max()).sort_index()[y]
    series = series.loc[series.index>val_thr]
    series_rolling_median = series.rolling(win).median()[::step]
    series_rolling_q75 = series.rolling(win).quantile(0.75)[::step]
    series_rolling_q25 = series.rolling(win).quantile(0.25)[::step]
    return series_rolling_median, series_rolling_q25, series_rolling_q75

def explore_feature_vs_target_and_preds(df: pd.DataFrame, x: str, win=10, step=10, val_thr=0.0):
    s_true, s_true_q25, s_true_q75 = calculate_dep(df, x, "target_per_capacity", win, step, val_thr)
    #s_p1, s_p1_q25, s_p1_q75 = calculate_dep(df, x, "predictions_first_order_per_capacity", win, step, val_thr)
    s_p2, s_p2_q25, s_p2_q75 = calculate_dep(df, x, "predictions_per_capacity", win, step, val_thr)

    fig = go.Figure(
        [
            go.Scattergl(
                x=s_true.index, 
                y=s_true,
                marker_color="blue",
                mode="markers", 
                hoverinfo="skip",
                name="targets_per_capacity"
            ),
            go.Scatter(
                x=s_true_q25.index,
                y=s_true_q25,
                mode='lines',
                marker=dict(color="#444"),
                line=dict(width=0),
                showlegend=False
            ),
            go.Scatter(
                x=s_true_q75.index,
                y=s_true_q75,
                marker=dict(color="#444"),
                line=dict(width=0),
                mode='lines',
                fillcolor='rgba(68, 68, 68, 0.3)',
                fill='tonexty',
                showlegend=False
            ),
            go.Scattergl(
                x=s_p2.index, 
                y=s_p2,
                marker_color="purple",
                mode="markers", 
                hoverinfo="skip",
                name="predictions_per_capacity"
            ),
        ]
    )

    return fig


explore_feature_vs_target_and_preds(df, "surface_solar_radiation_downwards_forecast", 150, 100)

In [169]:
df_insp_p = df.loc[
    (df["county"]==0) &
    (df["product_type"]==1) &
    (df["is_business"]==1) &
    (df["is_consumption"]==0)
]
df_insp_p

county is_business product_type is_consumption            datetime  \
row_id                                                                       
412856       0           1            1              0 2022-01-16 00:00:00   
412986       0           1            1              0 2022-01-16 01:00:00   
413116       0           1            1              0 2022-01-16 02:00:00   
413246       0           1            1              0 2022-01-16 03:00:00   
413376       0           1            1              0 2022-01-16 04:00:00   
...        ...         ...          ...            ...                 ...   
2017710      0           1            1              0 2023-05-31 19:00:00   
2017840      0           1            1              0 2023-05-31 20:00:00   
2017970      0           1            1              0 2023-05-31 21:00:00   
2018100      0           1            1              0 2023-05-31 22:00:00   
2018230      0           1            1              0 2023-05-31 23:00:00   

              date  dayofyear  hour  day  weekday  ...  \
row_id                                             ...   
412856  2022-01-16         16     0   16        7  ...   
412986  2022-01-16         16     1   16        7  ...   
413116  2022-01-16         16     2   16        7  ...   
413246  2022-01-16         16     3   16        7  ...   
413376  2022-01-16         16     4   16        7  ...   
...            ...        ...   ...  ...      ...  ...   
2017710 2023-05-31        151    19   31        3  ...   
2017840 2023-05-31        151    20   31        3  ...   
2017970 2023-05-31        151    21   31        3  ...   
2018100 2023-05-31        151    22   31        3  ...   
2018230 2023-05-31        151    23   31        3  ...   

         diff_168h_10_metre_v_wind_component_forecast  \
row_id                                                  
412856                                      -0.007749   
412986                                       1.566444   
413116                                       1.218801   
413246                                       1.310657   
413376                                       2.071204   
...                                               ...   
2017710                                     -1.406289   
2017840                                     -1.185897   
2017970                                     -0.819711   
2018100                                     -2.143498   
2018230                                     -1.831267   

         diff_168h_humidity_historical diff_168h_humidity_forecast  \
row_id                                                               
412856                       -2.644476                   89.139221   
412986                       -2.646803                   89.520805   
413116                       -2.879854                   -1.757038   
413246                       -3.903349                   -1.618537   
413376                       -4.833015                   -1.915879   
...                                ...                         ...   
2017710                      -1.086469                    2.961163   
2017840                      -5.386113                    0.446676   
2017970                      -5.548689                    1.733130   
2018100                      -7.578453                    0.846309   
2018230                      -9.441931                   -1.458280   

         diff_168h_fog_historical  diff_168h_fog_forecast  \
row_id                                                      
412856                   0.037245                0.360839   
412986                   0.034230                0.344308   
413116                  -0.003968                0.043219   
413246                  -0.031375                0.044108   
413376                  -0.033415                0.031023   
...                           ...                     ...   
2017710                 -0.168319               -0.202967   
2017840                 -0.199136   

In [170]:
viz_weather_and_predictions_for_month(df_insp_p, 2023, 4)

In [171]:
viz_weather_and_predictions_for_month(df_insp_p, 2023, 5)